<a href="https://colab.research.google.com/github/Maganti1205/earthengine-api/blob/master/demos/EarthEngineDemo_Final.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Demo Scenario

 Extreme weather events have a devastating impact around the world. Flooding, heat waves, and drought have substantial human and financial costs, causing mortality and devastation of homes and property. The following example shows how to use satellite data mosaics from Earth Engine and open road datasets from BigQuery, processing the data in both environments to determine which road segments are affected by a flooding event in the UK.


 ## Demo Flow

 Earth Engine => Big Query => Visualization

 ## Prerequisites


1.   Install the dependencies {--geemap , earthengine-api}
2.   Create a new GCP project and check that billing is enabled. Alternatively an existing project with valid billing ID could be used.
3.   Enable the BigQuery and Earth Engine APIs.
4.   Make sure to have the permissions to create dataset.
5.   Make sure to have the below IAM roles assigned on the Bigquery dataset

>1. bigquery.dataEditor + bigquery.jobUser

>2. bigquery.dataOwner + bigquery.jobUser

>3. bigquery.admin




























In [21]:
# @title Prerequisites
# Install 'geemap' libary to display the map
!pip install geemap
!pip install earthengine-api --upgrade

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [22]:
# @title Parameter Setup
project_id = "my-demo-project-360918"  # @param {type:"string"} #replace the project id with your project
dataset_id = "ee_export"
table_id = "ee_test"
table =  dataset_id + "." + table_id
region = 'us'
table_path = project_id + "." + dataset_id + "." + table_id
print("Region:      ",region)
print("Table Path:  ",table_path)


Region:       us
Table Path:   my-demo-project-360918.ee_export.ee_test


In [23]:
# @title Authenticate and initialize the Session
import google
import ee
from google.cloud import bigquery
from google.colab import auth as google_auth
client= bigquery.Client()
google_auth.authenticate_user()
credentials, auth_project_id = google.auth.default()
ee.Initialize(credentials, project=project_id)

In [ ]:
# @title Create BQ Dataset
# Create BQ Project
!bq --location={region} mk --dataset {project_id}:{dataset_id}

Define area of interest and centre point

In [24]:
# @title Define point and Area of Interest(aoi)
# Define aoi(Area of Interest) Polygon
aoi = ee.Geometry.Polygon([[-2.92, 54.10],
          [-2.92, 53.99],
          [-2.67, 53.99],
          [-2.67, 54.10]])

In [26]:
# @title Display aoi and point
import geemap
Map = geemap.Map()
Map.centerObject(aoi, 12);
Map.setOptions(mapTypeId='HYBRID', styles={}, types=[])
Map.addLayer(aoi,{"color":"blue"});
Map

Map(center=[54.04504054423635, -2.7949999999993755], controls=(ZoomControl(options=['position', 'zoom_in_text'…

The Earth Engine Data Catalog contains the [Copernicus Sentinel Synthetic Aperture Radar collection](https://colab.research.google.com/drive/11Cr9nqizvw4D-SwSKgV2mZ6njFiy1lac#scrollTo=ycom7Zl36R4I&line=1&uniqifier=1). This public dataset is composed of radar images that measure how surfaces scatter light waves back to a satellite's sensor. Standing bodies of water act like mirrors for radio signals, reflecting the satellite's radar light away rather than scattering it back to the imaging sensor. Most natural surfaces don't have this property, which means that one can differentiate standing bodies of water from their surroundings by looking for "dark" patches in the images (that is, areas with low backscatter values). Let’s prepare the input data by selecting an area of interest and filtering images with vertical-vertical ("VV") polarization, sending vertically polarized light, and measuring the vertically polarized light that's returned.

In [27]:
# @title Data Collections
# Load Sentinel-1 C-band SAR Ground Range collection (log scaling, VV co-polar)
collection = ee.ImageCollection('COPERNICUS/S1_GRD').filterBounds(aoi).filter(ee.Filter.listContains('transmitterReceiverPolarisation', 'VV')).select('VV')
# Smooth the data to remove noise.
smoothing_radius = 100
# Filter by date
before = collection.filterDate('2017-11-01', '2017-11-17').mosaic().focal_median(smoothing_radius, 'circle', 'meters') #before floods
after = collection.filterDate('2017-11-18', '2017-11-23').mosaic().focal_median(smoothing_radius, 'circle', 'meters') #after floods

In [28]:
# @title Identify Flooded Areas
# Threshold smoothed radar intensities to identify areas with standing water.
diff_upper_threshold = -3
diff_smoothed = after.subtract(before);
diff_thresholded = diff_smoothed.lt(diff_upper_threshold)

use the [Global Surface Water dataset](https://developers.google.com/earth-engine/tutorials/tutorial_global_surface_water_01) to remove persistent surface water (like lakes, rivers, etc.) from the result:

In [29]:
# @title Remove Water Areas(other than floods)
# Remove global surface water i.e oceans, lakes, etc
water_occ = ee.Image("JRC/GSW1_0/GlobalSurfaceWater").select('occurrence')
jrc_data0 = ee.Image("JRC/GSW1_0/Metadata").select('total_obs').lte(0)
water_occfilled = water_occ.unmask(0).max(jrc_data0)
water_mask = water_occfilled.lt(10)
diff_thresholded = diff_thresholded.updateMask(water_mask)

In [30]:
# @title Visualize the Map with Flooded Area
# Display flooded areas on the map
import geemap
vis_params = {
    "palette": ["blue"],
}
Map = geemap.Map()
Map.setOptions(mapTypeId='HYBRID', styles={}, types=[])
Map.centerObject(aoi, 12);
Map.addLayer(diff_thresholded.updateMask(diff_thresholded),vis_params,'flooded areas - blue', 1)
Map

Map(center=[54.04504054423635, -2.7949999999993755], controls=(ZoomControl(options=['position', 'zoom_in_text'…

We want the flooded areas in BigQuery, so let’s convert flooded pixel data to vector format.

In [11]:
# @title Extract Vectors from the Flooded areas
# Extract vectors from the diff threshold to load to Bigquery
vectors = diff_thresholded.reduceToVectors(geometry = aoi, scale = 10,geometryType = 'polygon',eightConnected = True)

This is where our new BigQuery connector simplifies export to just making one call: Export.table.toBigQuery.

In [12]:
# @title Export to BigQuery
task_config = { 'collection': vectors,
  'description':'ee2bq_export_polygons',
  'table': table_path,
  'overwrite': True
}
task = ee.batch.Export.table.toBigQuery(**task_config)
task.start() # after a few minutes it will be completed, check task.status() to see the result


In [ ]:
# @title Check Export Job Status
# Check the results and make sure the status is COMPLETED before checking the results in BigQuery
task.status()

Now we have exported data available in BigQuery. Execute the query to check the data

In [15]:
# @title Check Bigquery Results
%%bigquery --project $project_id
SELECT * from ee_export.ee_test #replace it with your dataset and tablename
# If you get a "table not found" error then check the step above to see if your job has completed

Query is running:   0%|          |

Downloading:   0%|          |

geo  count  label  \
0    POLYGON((-2.46964837910139 54.0320473722778, -...      1      0   
1    POLYGON((-2.735819197786 54.0746275167451, -2....      1      0   
2    POLYGON((-2.52444561143268 53.9792264335716, -...      1      0   
3    POLYGON((-2.45841943804989 54.0117454468567, -...      1      0   
4    POLYGON((-2.46389916128302 54.045162775426, -2...      1      0   
..                                                 ...    ...    ...   
436  POLYGON((-2.80130638199832 54.0296219210107, -...    250      1   
437  MULTIPOLYGON(((-2.53441691108641 54.0385152423...    506      1   
438  POLYGON((-2.53917798209224 54.0038402723564, -...    252      1   
439  POLYGON((-2.48842316853949 54.0032114516576, -...   3068      1   
440  POLYGON((-2.5501374285585 53.982819694708, -2....   3583      1   

      system:index  
0    -27492+601482  
1    -30455+601956  
2    -28102+600894  
3    -27367+601256  
4    -27428+601628  
..             ...  
436  -31182+601454  
437  -28193+601584  
438  -28265+601167  
439  -27698+601160  
440  -28401+600938  

[441 rows x 4 columns]

In our example we are going to use the public “planet_ways” dataset from OpenStreetMap, so we can find roads that are underwater.


> Get polygons corresponding to flat areas from the exported table.

> Filter out administrative areas

> Join result with road polygons from OpenStreetMap data that intersect with flat areas.


In [31]:
# @title BQ Result set to display flooded highways
%%bigquery regions_by_country --project $project_id
SELECT
 id, area,version,changeset,osm_timestamp,ST_ASGEOJSON(flood_poly) as flood_poly,
 ST_ASGEOJSON(road_geometry) as road_geometry
FROM (
 -- query 1 - find all the flooding areas
 SELECT
   geo AS flood_poly,
   ST_AREA(geo) AS area
 FROM
   ee_export.ee_test #replace it with your dataset and tablename
 WHERE
   ST_AREA(geo) < 500000 ) t1 -- eliminate admin areas in the dataset
JOIN (
 SELECT
   id,
   version,
   changeset,
   osm_timestamp,
   geometry as road_geometry
 FROM
   `bigquery-public-data.geo_openstreetmap.planet_ways` planet_ways,
   planet_ways.all_tags AS all_tags
 WHERE
   all_tags.key = 'highway' )
ON
 ST_INTERSECTS(flood_poly, road_geometry)

Query is running:   0%|          |

Downloading:   0%|          |

In [32]:
# @title Extract the Features from flood_poly
floods = '{"type": "FeatureCollection", "features":['
floods += regions_by_country.flood_poly.str.cat(sep=", ")
floods += ']}'

In [33]:
# @title Extract the features from road_geometry
highways = '{"type": "FeatureCollection", "features":['
highways += regions_by_country.road_geometry.str.cat(sep=", ")
highways += ']}'

In [34]:
# @title Display Flooded Areas and  Highways using geemap
import geemap
from ipyleaflet import GeoJSON
import json

styling = {"color":"red","fillcolor":"red"}

Flooded_Highways=GeoJSON(
    data=json.loads(floods),
    name='Flooded areas'
)

Flooded_Areas=GeoJSON(
    data=json.loads(highways),
    name='Flooded roads',
    style = styling
)
Map=geemap.Map()
Map.setOptions(mapTypeId='HYBRID', styles={}, types=[])
Map.centerObject(aoi, 12)
Map.add_layer(Flooded_Highways)
Map.add_layer(Flooded_Areas)
Map

Map(center=[54.04504054423635, -2.7949999999993755], controls=(ZoomControl(options=['position', 'zoom_in_text'…